In [1]:
import pandas as pd
from kmodes.kprototypes import KPrototypes
from sklearn.preprocessing import StandardScaler
import folium
from folium.plugins import MarkerCluster

In [2]:
df = pd.read_csv("enviroTab_pa_train.csv", sep=';')
df_sans_na = df.dropna()
df_sans_na.reset_index(inplace=True, drop=True)

In [3]:
quanti = df_sans_na.iloc[:,9:37]
variables_quantitatives = quanti.apply(lambda col: col.fillna(col.mean()), axis=0)

In [4]:
quanti.head()

bio1  bio2  bio3  bio4  bio5  bio6  bio7  bio8  bio9  bio10  ...  bio19  \
0  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
1  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
2  2878    95  3.33  6635  3032  2747   285  2880  2967   2967  ...   1559   
3  2876    95  3.33  6614  3031  2746   285  2879  2965   2965  ...   1603   
4  2877    95  3.33  6635  3031  2746   285  2879  2966   2966  ...   1586   

         bdod         cec        cfvo        clay    nitrogen      phh2o  \
0  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
1  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
2  142.439041  192.611618  173.934845  244.970306  184.283295  75.167183   
3  139.343964  201.281235  184.239105  223.070511  221.730957  73.108734   
4  145.295364  195.884705  171.115875  234.305283  195.522888  74.028191   

         sand        silt         soc  
0  379.648071  374.968933  226.862244  
1  379.648071  374.968933  226.862244  
2  379.648071  374.968933  226.862244  
3  378.273560  398.929901  255.015320  
4  382.905090  382.355530  241.613922  

[5 rows x 28 columns]

In [5]:
quali = df_sans_na[['landCov','Popdensity2010', 'Built2009', 'Lights2009', 'Railways', 'Roads']]
variables_qualitatives = quali.apply(lambda col: col.fillna(col.mode()[0]), axis=0)

In [6]:
scaler = StandardScaler()
variables_quantitatives_standardisees = scaler.fit_transform(variables_quantitatives)

# Concaténation des variables quantitatives standardisées et des variables catégorielles
X = pd.concat([pd.DataFrame(variables_quantitatives_standardisees, columns=variables_quantitatives.columns), variables_qualitatives], axis=1)

# Spécification du nombre de clusters (à ajuster)
nombre_clusters = 5

# Application de l'algorithme K-Prototypes
kproto = KPrototypes(n_clusters=nombre_clusters, init='Cao', verbose=2)
clusters = kproto.fit_predict(X, categorical=[X.columns.get_loc(col) for col in variables_qualitatives.columns])

# Ajout des étiquettes de cluster au DataFrame d'origine
df_sans_na['cluster'] = clusters

Initialization method and algorithm are deterministic. Setting n_init to 1.
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 1, iteration: 1/100, moves: 2450, ncost: 75554.64183281346
Run: 1, iteration: 2/100, moves: 601, ncost: 72570.67554567472
Run: 1, iteration: 3/100, moves: 548, ncost: 70528.7834630813
Run: 1, iteration: 4/100, moves: 401, ncost: 69333.10119712683
Run: 1, iteration: 5/100, moves: 191, ncost: 69061.5587883159
Run: 1, iteration: 6/100, moves: 175, ncost: 68785.94049619407
Run: 1, iteration: 7/100, moves: 113, ncost: 68644.65985209594
Run: 1, iteration: 8/100, moves: 55, ncost: 68566.1534385994
Run: 1, iteration: 9/100, moves: 15, ncost: 68561.35238445869
Run: 1, iteration: 10/100, moves: 3, ncost: 68561.02540551669
Run: 1, iteration: 11/100, moves: 0, ncost: 68561.02540551669
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 2, iteration: 1/100, moves: 1801, ncost: 75740.34744933475
Run: 2, itera

C:\Users\Utilisateur\AppData\Local\Temp\ipykernel_8824\312485815.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_sans_na['cluster'] = clusters


In [15]:
import folium

# Supposons que vous avez déjà les résultats et les données de test
# Assurez-vous que les indices correspondent entre result et test_df

# Initialisation des variables pour la carte
m = folium.Map(location=[df_sans_na['lat'].mean(), df_sans_na['lon'].mean()], zoom_start=10)

# Créez une fonction pour attribuer une couleur en fonction du cluster
def assign_color(cluster):
    # Ajoutez autant de couleurs que de clusters possibles
    color_mapping = {
        0: 'darkblue',
        1: 'lightblue',
        2: 'lightred',
        3: 'lightgreen',
        4: 'purple',
        # Ajoutez d'autres couleurs au besoin
    }
    # Utilisez la couleur par défaut si le cluster n'est pas dans la carte
    return color_mapping.get(cluster, 'gray')

# Ajoutez les marqueurs à la carte en utilisant les coordonnées et la couleur du cluster
for index, row in df_sans_na.iterrows():
    cluster_color = assign_color(row['cluster'])
    folium.Marker(
        location=[row['lat'], row['lon']],
        popup=f"Cluster: {row['cluster']}",
        icon=folium.Icon(color=cluster_color)
    ).add_to(m)

# Sauvegardez la carte au format HTML
m.save("carte.html")

# Affichez la carte
m



In [14]:
for val in clusters :
    if val > 0 :
        print(val)

2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
2
2
2
2
2
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
2
1
2
2
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
1
2
2
